<h1>Analyzing System Logs for Anomaly Detection</h1>

This script shows a system logs for anomaly detection. Both **supervised learning** (e.g., logistic regression, decision tree, SVM) and **unsupervised learning** (clustering, PCA, invariants mining) methods have been used for the task of anomaly detection. In this example, we use supervised learning, specifically, a **logistic regression model** and a **decision tree model**, to indentify anomalies in system logs.

Log-based anomaly detection typically include four steps: **log collection**, **log parsing**, **feature extraction**, and **anomaly detection**. In this demo, we focus on the **feature extraction** and **anomaly detection** steps.

## Import needed libraries and dependencies

Import the needed libraries. We use the **logistic regression model** and the **decision tree model** provided by the **sklearn** library. We use the **numpy** and **pandas** libraries to deal with basic data structures (e.g., arrays and dataframes) used in our analysis.

In [51]:
from sklearn.linear_model import LogisticRegression
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import precision_recall_fscore_support
from sklearn.metrics import precision_recall_curve
from sklearn.metrics import roc_auc_score
from sklearn.metrics import roc_curve
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
import re
from sklearn.utils import shuffle
from collections import OrderedDict
from collections import Counter
from logparser.Drain import LogParser
from logparser.Drain import LogParser

## Parse unstructured log data into structured data


In [3]:
input_dir = 'dataset/BGL' # The input directory of log file
output_dir = 'result/BGL'  # The output directory of parsing results
log_file = 'BGL.log'  # The input log file name
log_format = '<Label> <Timestamp> <Date> <Node> <Time> <NodeRepeat> <Type> <Component> <Level> <Content>'  # BGL log format
regex = [
    r'core\.\d+',
    r'(?<=r)\d{1,2}',
    r'(?<=fpr)\d{1,2}',
    r'(0x)?[0-9a-fA-F]{8}',
    r'(?<=\.\.)0[xX][0-9a-fA-F]+',
    r'(?<=\.\.)\d+(?!x)',
    r'\d+(?=:)',
    r'^\d+$',  #only numbers
    r'(?<=\=)\d+(?!x)',
    r'(?<=\=)0[xX][0-9a-fA-F]+',
    r'(?<=\ )[A-Z][\+|\-](?= |$)',
    r'(?<=:\ )[A-Z](?= |$)',
    r'(?<=\ [A-Z]\ )[A-Z](?= |$)'
]

st = 0.5  # Similarity threshold
depth = 4  # Depth of all leaf nodes

parser = LogParser(log_format, indir=input_dir, outdir=output_dir,  depth=depth, st=st, rex=regex)
parser.parse(log_file)

Parsing file: dataset/BGL/BGL.log
[Warning] Skip line: - 1120866514 2005.07.08 R02-M1-N8-C:J13-U01 2005-07-08-16.48.34.004234 R02-M1-N8-C:J13-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R35-M1-N0-C:J12-U11 2005-07-08-16.48.34.031730 R35-M1-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R36-M0-NC-C:J12-U01 2005-07-08-16.48.34.080039 R36-M0-NC-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R36-M0-N0-C:J12-U11 2005-07-08-16.48.34.130389 R36-M0-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R31-M0-N0-C:J16-U01 2005-07-08-16.48.34.260738 R31-M0-N0-C:J16-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R31-M0-N0-C:J12-U01 2005-07-08-16.48.34.288842 R31-M0-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R22-M1-NC-C:J16-U01 2005-07-08-16.48.34.357656 R22-M1-NC-C:J16-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1120866514 2005.07.08 R27-M0-N0-C

[Warning] Skip line: - 1121124512 2005.07.11 R31-M0-N4-C:J16-U01 2005-07-11-16.28.32.568308 R31-M0-N4-C:J16-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R36-M0-N4-C:J12-U01 2005-07-11-16.28.32.597824 R36-M0-N4-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R33-M0-NC-C:J12-U01 2005-07-11-16.28.32.626556 R33-M0-NC-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R30-M0-N0-C:J12-U11 2005-07-11-16.28.32.675552 R30-M0-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R30-M0-N0-C:J12-U01 2005-07-11-16.28.32.695689 R30-M0-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R20-M1-NC-C:J12-U01 2005-07-11-16.28.32.752304 R20-M1-NC-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R33-M0-N4-C:J12-U01 2005-07-11-16.28.32.809597 R33-M0-N4-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121124512 2005.07.11 R34-M0-N0-C:J16-U01 2005-07-11-16.28.32.82929

[Warning] Skip line: - 1121464496 2005.07.15 R36-M0-N0-C:J12-U01 2005-07-15-14.54.56.354027 R36-M0-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121464497 2005.07.15 R20-M1-N0-C:J12-U11 2005-07-15-14.54.57.627541 R20-M1-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1121464497 2005.07.15 R20-M1-N0-C:J12-U01 2005-07-15-14.54.57.654094 R20-M1-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121464497 2005.07.15 R37-M0-N0-C:J12-U11 2005-07-15-14.54.57.764160 R37-M0-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1121464498 2005.07.15 R25-M0-N0-C:J12-U01 2005-07-15-14.54.58.679790 R25-M0-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121464498 2005.07.15 R24-M0-N8-C:J12-U01 2005-07-15-14.54.58.776766 R24-M0-N8-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1121464498 2005.07.15 R27-M1-N0-C:J12-U11 2005-07-15-14.54.58.951065 R27-M1-N0-C:J12-U11 RAS KERNEL FATAL

[Warning] Skip line: - 1121464498 2005.07.15 R27-M1-N0-C:J12-U01 2005-07-15-14.54.58.97847

[Warning] Skip line: - 1122322449 2005.07.25 R36-M0-N8-C:J12-U01 2005-07-25-13.14.09.942613 R36-M0-N8-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322449 2005.07.25 R36-M0-N4-C:J16-U01 2005-07-25-13.14.09.962716 R36-M0-N4-C:J16-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322449 2005.07.25 R22-M1-N0-C:J16-U01 2005-07-25-13.14.09.982019 R22-M1-N0-C:J16-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322450 2005.07.25 R20-M1-N0-C:J12-U01 2005-07-25-13.14.10.001445 R20-M1-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322450 2005.07.25 R20-M1-NC-C:J12-U01 2005-07-25-13.14.10.020363 R20-M1-NC-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322450 2005.07.25 R24-M0-N0-C:J12-U01 2005-07-25-13.14.10.039175 R24-M0-N0-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322450 2005.07.25 R20-M0-NC-C:J12-U01 2005-07-25-13.14.10.058303 R20-M0-NC-C:J12-U01 RAS KERNEL FATAL

[Warning] Skip line: - 1122322450 2005.07.25 R24-M1-N0-C:J16-U01 2005-07-25-13.14.10.08006

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J09-U11 2005-08-26-12.03.51.683915 R63-M1-N7-C:J09-U11 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J15-U11 2005-08-26-12.03.51.723662 R63-M1-N7-C:J15-U11 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J11-U11 2005-08-26-12.03.51.745138 R63-M1-N7-C:J11-U11 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J13-U11 2005-08-26-12.03.51.759643 R63-M1-N7-C:J13-U11 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J17-U11 2005-08-26-12.03.51.775296 R63-M1-N7-C:J17-U11 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J05-U01 2005-08-26-12.03.51.801391 R63-M1-N7-C:J05-U01 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J03-U01 2005-08-26-12.03.51.816937 R63-M1-N7-C:J03-U01 RAS KERNEL INFO

[Warning] Skip line: - 1125083031 2005.08.26 R63-M1-N7-C:J05-U11 2005-08-26-12.03.51.831427 R63-M

...

Processed 76.0% of log lines.
Processed 76.0% of log lines.
Processed 76.0% of log lines.
Processed 76.0% of log lines.
Processed 76.1% of log lines.
Processed 76.1% of log lines.
Processed 76.1% of log lines.
Processed 76.1% of log lines.
Processed 76.1% of log lines.
Processed 76.2% of log lines.
Processed 76.2% of log lines.
Processed 76.2% of log lines.
Processed 76.2% of log lines.
Processed 76.2% of log lines.
Processed 76.3% of log lines.
Processed 76.3% of log lines.
Processed 76.3% of log lines.
Processed 76.3% of log lines.
Processed 76.4% of log lines.
Processed 76.4% of log lines.
Processed 76.4% of log lines.
Processed 76.4% of log lines.
Processed 76.4% of log lines.
Processed 76.5% of log lines.
Processed 76.5% of log lines.
Processed 76.5% of log lines.
Processed 76.5% of log lines.
Processed 76.5% of log lines.
Processed 76.6% of log lines.
Processed 76.6% of log lines.
Processed 76.6% of log lines.
Processed 76.6% of log lines.
Processed 76.7% of log lines.
Processed 

Processed 81.8% of log lines.
Processed 81.8% of log lines.
Processed 81.8% of log lines.
Processed 81.9% of log lines.
Processed 81.9% of log lines.
Processed 81.9% of log lines.
Processed 81.9% of log lines.
Processed 81.9% of log lines.
Processed 82.0% of log lines.
Processed 82.0% of log lines.
Processed 82.0% of log lines.
Processed 82.0% of log lines.
Processed 82.0% of log lines.
Processed 82.1% of log lines.
Processed 82.1% of log lines.
Processed 82.1% of log lines.
Processed 82.1% of log lines.
Processed 82.1% of log lines.
Processed 82.2% of log lines.
Processed 82.2% of log lines.
Processed 82.2% of log lines.
Processed 82.2% of log lines.
Processed 82.3% of log lines.
Processed 82.3% of log lines.
Processed 82.3% of log lines.
Processed 82.3% of log lines.
Processed 82.3% of log lines.
Processed 82.4% of log lines.
Processed 82.4% of log lines.
Processed 82.4% of log lines.
Processed 82.4% of log lines.
Processed 82.4% of log lines.
Processed 82.5% of log lines.
Processed 

Processed 87.6% of log lines.
Processed 87.6% of log lines.
Processed 87.6% of log lines.
Processed 87.7% of log lines.
Processed 87.7% of log lines.
Processed 87.7% of log lines.
Processed 87.7% of log lines.
Processed 87.7% of log lines.
Processed 87.8% of log lines.
Processed 87.8% of log lines.
Processed 87.8% of log lines.
Processed 87.8% of log lines.
Processed 87.9% of log lines.
Processed 87.9% of log lines.
Processed 87.9% of log lines.
Processed 87.9% of log lines.
Processed 87.9% of log lines.
Processed 88.0% of log lines.
Processed 88.0% of log lines.
Processed 88.0% of log lines.
Processed 88.0% of log lines.
Processed 88.0% of log lines.
Processed 88.1% of log lines.
Processed 88.1% of log lines.
Processed 88.1% of log lines.
Processed 88.1% of log lines.
Processed 88.2% of log lines.
Processed 88.2% of log lines.
Processed 88.2% of log lines.
Processed 88.2% of log lines.
Processed 88.2% of log lines.
Processed 88.3% of log lines.
Processed 88.3% of log lines.
Processed 

Processed 93.4% of log lines.
Processed 93.4% of log lines.
Processed 93.5% of log lines.
Processed 93.5% of log lines.
Processed 93.5% of log lines.
Processed 93.5% of log lines.
Processed 93.5% of log lines.
Processed 93.6% of log lines.
Processed 93.6% of log lines.
Processed 93.6% of log lines.
Processed 93.6% of log lines.
Processed 93.6% of log lines.
Processed 93.7% of log lines.
Processed 93.7% of log lines.
Processed 93.7% of log lines.
Processed 93.7% of log lines.
Processed 93.8% of log lines.
Processed 93.8% of log lines.
Processed 93.8% of log lines.
Processed 93.8% of log lines.
Processed 93.8% of log lines.
Processed 93.9% of log lines.
Processed 93.9% of log lines.
Processed 93.9% of log lines.
Processed 93.9% of log lines.
Processed 93.9% of log lines.
Processed 94.0% of log lines.
Processed 94.0% of log lines.
Processed 94.0% of log lines.
Processed 94.0% of log lines.
Processed 94.0% of log lines.
Processed 94.1% of log lines.
Processed 94.1% of log lines.
Processed 

Processed 99.2% of log lines.
Processed 99.3% of log lines.
Processed 99.3% of log lines.
Processed 99.3% of log lines.
Processed 99.3% of log lines.
Processed 99.4% of log lines.
Processed 99.4% of log lines.
Processed 99.4% of log lines.
Processed 99.4% of log lines.
Processed 99.4% of log lines.
Processed 99.5% of log lines.
Processed 99.5% of log lines.
Processed 99.5% of log lines.
Processed 99.5% of log lines.
Processed 99.5% of log lines.
Processed 99.6% of log lines.
Processed 99.6% of log lines.
Processed 99.6% of log lines.
Processed 99.6% of log lines.
Processed 99.7% of log lines.
Processed 99.7% of log lines.
Processed 99.7% of log lines.
Processed 99.7% of log lines.
Processed 99.7% of log lines.
Processed 99.8% of log lines.
Processed 99.8% of log lines.
Processed 99.8% of log lines.
Processed 99.8% of log lines.
Processed 99.8% of log lines.
Processed 99.9% of log lines.
Processed 99.9% of log lines.
Processed 99.9% of log lines.
Processed 99.9% of log lines.
Processed 

## Read the parsed (strutured) log data

In [52]:
# Use parse file
struct_log_file = 'result/BGL/BGL.log_structured.csv'

In [53]:
# read the csv files into Pandas dataframes
struct_log_file = struct_log_file
struct_log = pd.read_csv(struct_log_file, engine='c', na_filter=False, memory_map=True)
# label_data = pd.read_csv(label_file, engine='c', na_filter=False, memory_map=True)

### Exploring the data
It is always a good practice to explore the data before doing any analysis.

In [54]:
print(type(struct_log))
print(struct_log.shape)
struct_log.head(10000)

<class 'pandas.core.frame.DataFrame'>
(4713493, 14)


LineId Label   Timestamp        Date                 Node  \
0          1     -  1117838570  2005.06.03  R02-M1-N0-C:J12-U11   
1          2     -  1117838570  2005.06.03  R02-M1-N0-C:J12-U11   
2          3     -  1117838570  2005.06.03  R02-M1-N0-C:J12-U11   
3          4     -  1117838570  2005.06.03  R02-M1-N0-C:J12-U11   
4          5     -  1117838570  2005.06.03  R02-M1-N0-C:J12-U11   
...      ...   ...         ...         ...                  ...   
9995    9996     -  1117845126  2005.06.03  R21-M1-NE-C:J07-U11   
9996    9997     -  1117845126  2005.06.03  R21-M1-NE-C:J17-U01   
9997    9998     -  1117845126  2005.06.03  R21-M1-NE-C:J07-U01   
9998    9999     -  1117845126  2005.06.03  R21-M1-NE-C:J09-U01   
9999   10000     -  1117845126  2005.06.03  R21-M1-NE-C:J16-U11   

                            Time           NodeRepeat Type Component Level  \
0     2005-06-03-15.42.50.363779  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
1     2005-06-03-15.42.50.527847  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
2     2005-06-03-15.42.50.675872  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
3     2005-06-03-15.42.50.823719  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
4     2005-06-03-15.42.50.982731  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
...                          ...                  ...  ...       ...   ...   
9995  2005-06-03-17.32.06.012050  R21-M1-NE-C:J07-U11  RAS    KERNEL  INFO   
9996  2005-06-03-17.32.06.031576  R21-M1-NE-C:J17-U01  RAS    KERNEL  INFO   
9997  2005-06-03-17.32.06.050726  R21-M1-NE-C:J07-U01  RAS    KERNEL  INFO   
9998  2005-06-03-17.32.06.069979  R21-M1-NE-C:J09-U01  RAS    KERNEL  INFO   
9999  2005-06-03-17.32.06.101496  R21-M1-NE-C:J16-U11  RAS    KERNEL  INFO   

                                       Content   EventId  \
0     instruction cache parity error corrected  3aa50e45   
1     instruction cache parity error corrected  3aa50e45   
2     instruction cache parity error corrected  3aa50e45   
3     instruction cache parity error corrected  3aa50e45   
4     instruction cache parity error corrected  3aa50e45   
...                                        ...       ...   
9995                      generating core.1182  070de4aa   
9996                      generating core.1044  070de4aa   
9997                      generating core.1174  070de4aa   
9998                      generating core.1046  070de4aa   
9999                      generating core.1036  070de4aa   

                                 EventTemplate  ParameterList  
0     instruction cache parity error corrected             []  
1     instruction cache parity error corrected             []  
2     instruction cache parity error corrected             []  
3     instruction cache parity error corrected             []  
4     instruction cache parity error corrected             []  
...                                        ...            ...  
9995                            generating <*>  ['core.1182']  
9996                            generating <*>  ['core.1044']  
9997                            generating <*>  ['core.1174']  
9998                            generating <*>  ['core.1046']  
9999                            generating <*>  ['core.1036']  

[10000 rows x 14 columns]

## Preprocessing the data
This step group logs into sessions based on the time window (6 hours).

### Attribute window-based grouping

In [55]:
session_duration = pd.Timedelta(hours=6)
struct_log['Timestamp'] = pd.to_datetime(struct_log['Timestamp'], unit='s')  # Convert to datetime

timestamp_start = struct_log['Timestamp'].min()

struct_log['Session'] = ((struct_log['Timestamp'] - timestamp_start) / session_duration).astype(int)

print(type(struct_log))
print(struct_log.shape)
struct_log.head(10)

<class 'pandas.core.frame.DataFrame'>
(4713493, 15)


LineId Label           Timestamp        Date                 Node  \
0       1     - 2005-06-03 22:42:50  2005.06.03  R02-M1-N0-C:J12-U11   
1       2     - 2005-06-03 22:42:50  2005.06.03  R02-M1-N0-C:J12-U11   
2       3     - 2005-06-03 22:42:50  2005.06.03  R02-M1-N0-C:J12-U11   
3       4     - 2005-06-03 22:42:50  2005.06.03  R02-M1-N0-C:J12-U11   
4       5     - 2005-06-03 22:42:50  2005.06.03  R02-M1-N0-C:J12-U11   
5       6     - 2005-06-03 22:42:51  2005.06.03  R02-M1-N0-C:J12-U11   
6       7     - 2005-06-03 22:42:51  2005.06.03  R02-M1-N0-C:J12-U11   
7       8     - 2005-06-03 22:42:51  2005.06.03  R02-M1-N0-C:J12-U11   
8       9     - 2005-06-03 22:42:51  2005.06.03  R02-M1-N0-C:J12-U11   
9      10     - 2005-06-03 22:42:51  2005.06.03  R02-M1-N0-C:J12-U11   

                         Time           NodeRepeat Type Component Level  \
0  2005-06-03-15.42.50.363779  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
1  2005-06-03-15.42.50.527847  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
2  2005-06-03-15.42.50.675872  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
3  2005-06-03-15.42.50.823719  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
4  2005-06-03-15.42.50.982731  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
5  2005-06-03-15.42.51.131467  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
6  2005-06-03-15.42.51.293532  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
7  2005-06-03-15.42.51.428563  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
8  2005-06-03-15.42.51.601412  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   
9  2005-06-03-15.42.51.749199  R02-M1-N0-C:J12-U11  RAS    KERNEL  INFO   

                                    Content   EventId  \
0  instruction cache parity error corrected  3aa50e45   
1  instruction cache parity error corrected  3aa50e45   
2  instruction cache parity error corrected  3aa50e45   
3  instruction cache parity error corrected  3aa50e45   
4  instruction cache parity error corrected  3aa50e45   
5  instruction cache parity error corrected  3aa50e45   
6  instruction cache parity error corrected  3aa50e45   
7  instruction cache parity error corrected  3aa50e45   
8  instruction cache parity error corrected  3aa50e45   
9  instruction cache parity error corrected  3aa50e45   

                              EventTemplate ParameterList  Session  
0  instruction cache parity error corrected            []        0  
1  instruction cache parity error corrected            []        0  
2  instruction cache parity error corrected            []        0  
3  instruction cache parity error corrected            []        0  
4  instruction cache parity error corrected            []        0  
5  instruction cache parity error corrected            []        0  
6  instruction cache parity error corrected            []        0  
7  instruction cache parity error corrected            []        0  
8  instruction cache parity error corrected            []        0  
9  instruction cache parity error corrected            []        0

### Extracting the event sequence

In [56]:
data_df = struct_log.groupby('Session')['EventId'].apply(list).reset_index()

data_df.columns = ['Session', 'EventSequence']

print(type(data_df))
print(data_df.shape)
data_df.head(5)

<class 'pandas.core.frame.DataFrame'>
(826, 2)


Session                                      EventSequence
0        0  [3aa50e45, 3aa50e45, 3aa50e45, 3aa50e45, 3aa50...
1        1  [d3e73bc3, 60b301fc, d3e73bc3, d3e73bc3, d3e73...
2        2  [4983ff07, 4983ff07, 150b1306, 150b1306, 150b1...
3        3           [3aa50e45, 3aa50e45, ba77ab8e, ba77ab8e]
4        4  [ba77ab8e, d3e73bc3, d3e73bc3, d3e73bc3, d3e73...

### Merging the label with the event sequence data

In [57]:
anomaly_event_ids = set(struct_log[struct_log['Label'] != '-']['EventId'])

def is_anomaly(event_sequence):
    return any(event in anomaly_event_ids for event in event_sequence)

data_df['Label'] = data_df['EventSequence'].apply(lambda x: 1 if is_anomaly(x) else 0)
                
data_df.head(5)

data_df.df.to_csv('result/BCG/BCG_ReadToMC.csv', index=False)

Session                                      EventSequence  Label
0        0  [3aa50e45, 3aa50e45, 3aa50e45, 3aa50e45, 3aa50...      0
1        1  [d3e73bc3, 60b301fc, d3e73bc3, d3e73bc3, d3e73...      1
2        2  [4983ff07, 4983ff07, 150b1306, 150b1306, 150b1...      1
3        3           [3aa50e45, 3aa50e45, ba77ab8e, ba77ab8e]      0
4        4  [ba77ab8e, d3e73bc3, d3e73bc3, d3e73bc3, d3e73...      0

### Spliting the data into training and testing subsets
We split the data into 80% training data and 20% testing data.

In [58]:
def _split_data(x_data, y_data, train_ratio=0.8):
    pos_idx = y_data > 0
    x_pos = x_data[pos_idx]
    y_pos = y_data[pos_idx]
    x_neg = x_data[~pos_idx]
    y_neg = y_data[~pos_idx]
    train_pos = int(train_ratio * x_pos.shape[0])
    train_neg = int(train_ratio * x_neg.shape[0])
    x_train = np.hstack([x_pos[0:train_pos], x_neg[0:train_neg]])
    y_train = np.hstack([y_pos[0:train_pos], y_neg[0:train_neg]])
    x_test = np.hstack([x_pos[train_pos:], x_neg[train_neg:]])
    y_test = np.hstack([y_pos[train_pos:], y_neg[train_neg:]])

    return (x_train, y_train), (x_test, y_test)

Shuffle and split the data into 70% training and 30% testing data.

In [59]:
# Shuffle the data
data_df = data_df.sample(frac=1).reset_index(drop=True)
data_df.head(5)

Session                                      EventSequence  Label
0      476  [5569cffc, 5569cffc, d3e73bc3, c39154ae, d6e5f...      0
1      659  [f97e57f1, f97e57f1, f97e57f1, f97e57f1, 7d268...      1
2      118  [ba77ab8e, 4ccdacef, fe297487, d3e73bc3, d3e73...      0
3      703  [71fcff11, 60b301fc, 60b301fc, 8df7ac9e, 5ada3...      1
4      588  [c39154ae, c39154ae, c39154ae, d3e73bc3, 60b30...      1

In [60]:
# Split train and test data
train_ratio = 0.8
(x_train, y_train), (x_test, y_test) = _split_data(data_df['EventSequence'].values,
    data_df['Label'].values, train_ratio)

Summarized the training and testing data.

In [61]:
num_train = x_train.shape[0]
num_test = x_test.shape[0]
num_total = num_train + num_test
num_train_pos = sum(y_train)
num_test_pos = sum(y_test)
num_pos = num_train_pos + num_test_pos

print('Total: {} instances, {} anomaly, {} normal' \
      .format(num_total, num_pos, num_total - num_pos))
print('Train: {} instances, {} anomaly, {} normal' \
      .format(num_train, num_train_pos, num_train - num_train_pos))
print('Test: {} instances, {} anomaly, {} normal\n' \
      .format(num_test, num_test_pos, num_test - num_test_pos))

#print(type(x_train))
print('====== x_train (first five lines) ======')
print(x_train[:5])

print('====== y_train (first five lines) ======')
print(y_train[:5])

Total: 826 instances, 417 anomaly, 409 normal
Train: 660 instances, 333 anomaly, 327 normal
Test: 166 instances, 84 anomaly, 82 normal

====== x_train (first five lines) ======
[list(['f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', '7d268245', '7d268245', '7d268245', '7d268245', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'f97e57f1', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'cc5f7485', 'a2335b6b', '9d5d6232', 'a2335b6b', 'a814cc3b', '9d5d6232', 'a814cc3b', 'cc5f7485', 'a2335b6b', '9d5d6232', 'a2335b6b', 'a814cc3b', '9d5d6232', 'a814cc3b', 'cc5f7485', 'a2335b6b', '9d5d6232', 'a2335b6b', 'a814cc3b', '9d5d6232', 'a814cc3b', 